<a href="https://colab.research.google.com/github/Matendy12/Project-4/blob/main/IMDB_Movies_Kmeans_Model.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install hvplot holoviews


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.8/6.8 MB 14.6 MB/s eta 0:00:00
  Attempting uninstall: bokeh
    Found existing installation: bokeh 3.4.1
    Uninstalling bokeh-3.4.1:
      Successfully uninstalled bokeh-3.4.1


In [ ]:
!pip install -U bokeh

  Using cached bokeh-3.4.1-py3-none-any.whl (7.0 MB)
  Attempting uninstall: bokeh
    Found existing installation: bokeh 3.3.4
    Uninstalling bokeh-3.3.4:
      Successfully uninstalled bokeh-3.3.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
panel 1.3.8 requires bokeh<3.4.0,>=3.2.0, but you have bokeh 3.4.1 which is incompatible.


In [ ]:
!pip install pandas scikit-learn

In [ ]:

# IMPORTANT: RUN THIS CELL IN ORDER TO IMPORT YOUR KAGGLE DATA SOURCES
# TO THE CORRECT LOCATION (/kaggle/input) IN YOUR NOTEBOOK,
# THEN FEEL FREE TO DELETE THIS CELL.
# NOTE: THIS NOTEBOOK ENVIRONMENT DIFFERS FROM KAGGLE'S PYTHON
# ENVIRONMENT SO THERE MAY BE MISSING LIBRARIES USED BY YOUR
# NOTEBOOK.

import os
import sys
from tempfile import NamedTemporaryFile
from urllib.request import urlopen
from urllib.parse import unquote, urlparse
from urllib.error import HTTPError
from zipfile import ZipFile
import tarfile
import shutil

CHUNK_SIZE = 40960
DATA_SOURCE_MAPPING = 'imdb-dataset-of-top-1000-movies-and-tv-shows:https%3A%2F%2Fstorage.googleapis.com%2Fkaggle-data-sets%2F1131493%2F1898721%2Fbundle%2Farchive.zip%3FX-Goog-Algorithm%3DGOOG4-RSA-SHA256%26X-Goog-Credential%3Dgcp-kaggle-com%2540kaggle-161607.iam.gserviceaccount.com%252F20240420%252Fauto%252Fstorage%252Fgoog4_request%26X-Goog-Date%3D20240420T205121Z%26X-Goog-Expires%3D259200%26X-Goog-SignedHeaders%3Dhost%26X-Goog-Signature%3D572c2982aabdb133839f97e2994a7f1a672c03aa0262eeaa2a806e8019b2e29a82c2a0900016d8d1f5e8a803d74988c2b8138cd6381463b68d4e72275a79710be273858c6befc666734905de8aaa8c1bc01ee1ba032743cd7c483f061a24d9035cb59a4f73d035fcaa4b629d57ffa3c01b1c67a987a44b647a6a222fdcbdc4cf1a1a4851f6cbb698a46a523c14a0cb155dc1dfe7e4312c9fbb2cc56f6b2e390163fade3752addd59bcece8d6cfdd7e73c9e6b51e87d36f649c1452de053805af1c52192b4859293cf1641c3f01d6e7749ed8935c474c075d4d0fd90e80283f169421349032f92242da9ab0ba892bcdd146d6318fed73cddab61106a26cf2e5c7'

KAGGLE_INPUT_PATH='/kaggle/input'
KAGGLE_WORKING_PATH='/kaggle/working'
KAGGLE_SYMLINK='kaggle'

!umount /kaggle/input/ 2> /dev/null
shutil.rmtree('/kaggle/input', ignore_errors=True)
os.makedirs(KAGGLE_INPUT_PATH, 0o777, exist_ok=True)
os.makedirs(KAGGLE_WORKING_PATH, 0o777, exist_ok=True)

try:
  os.symlink(KAGGLE_INPUT_PATH, os.path.join("..", 'input'), target_is_directory=True)
except FileExistsError:
  pass
try:
  os.symlink(KAGGLE_WORKING_PATH, os.path.join("..", 'working'), target_is_directory=True)
except FileExistsError:
  pass

for data_source_mapping in DATA_SOURCE_MAPPING.split(','):
    directory, download_url_encoded = data_source_mapping.split(':')
    download_url = unquote(download_url_encoded)
    filename = urlparse(download_url).path
    destination_path = os.path.join(KAGGLE_INPUT_PATH, directory)
    try:
        with urlopen(download_url) as fileres, NamedTemporaryFile() as tfile:
            total_length = fileres.headers['content-length']
            print(f'Downloading {directory}, {total_length} bytes compressed')
            dl = 0
            data = fileres.read(CHUNK_SIZE)
            while len(data) > 0:
                dl += len(data)
                tfile.write(data)
                done = int(50 * dl / int(total_length))
                sys.stdout.write(f"\r[{'=' * done}{' ' * (50-done)}] {dl} bytes downloaded")
                sys.stdout.flush()
                data = fileres.read(CHUNK_SIZE)
            if filename.endswith('.zip'):
              with ZipFile(tfile) as zfile:
                zfile.extractall(destination_path)
            else:
              with tarfile.open(tfile.name) as tarfile:
                tarfile.extractall(destination_path)
            print(f'\nDownloaded and uncompressed: {directory}')
    except HTTPError as e:
        print(f'Failed to load (likely expired) {download_url} to path {destination_path}')
        continue
    except OSError as e:
        print(f'Failed to load {download_url} to path {destination_path}')
        continue

print('Data source import complete.')

[==================================================] 179262 bytes downloaded
Downloaded and uncompressed: imdb-dataset-of-top-1000-movies-and-tv-shows
Data source import complete.


In [ ]:
# Import required libraries and dependencies
import pandas as pd
import hvplot.pandas
import holoviews as hv
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
#from itables import init_notebook_mode
#init_notebook_mode(all_interactive = True)
import warnings
warnings.filterwarnings('ignore')

In [ ]:
movies_df= pd.read_csv('/kaggle/input/imdb-dataset-of-top-1000-movies-and-tv-shows/imdb_top_1000.csv')

# Display sample data
movies_df.head(10)

Poster_Link  \
0  https://m.media-amazon.com/images/M/MV5BMDFkYT...   
1  https://m.media-amazon.com/images/M/MV5BM2MyNj...   
2  https://m.media-amazon.com/images/M/MV5BMTMxNT...   
3  https://m.media-amazon.com/images/M/MV5BMWMwMG...   
4  https://m.media-amazon.com/images/M/MV5BMWU4N2...   
5  https://m.media-amazon.com/images/M/MV5BNzA5ZD...   
6  https://m.media-amazon.com/images/M/MV5BNGNhMD...   
7  https://m.media-amazon.com/images/M/MV5BNDE4OT...   
8  https://m.media-amazon.com/images/M/MV5BMjAxMz...   
9  https://m.media-amazon.com/images/M/MV5BMmEzNT...   

                                    Series_Title Released_Year Certificate  \
0                       The Shawshank Redemption          1994           A   
1                                  The Godfather          1972           A   
2                                The Dark Knight          2008          UA   
3                         The Godfather: Part II          1974           A   
4                                   12 Angry Men          1957           U   
5  The Lord of the Rings: The Return of the King          2003           U   
6                                   Pulp Fiction          1994           A   
7                               Schindler's List          1993           A   
8                                      Inception          2010          UA   
9                                     Fight Club          1999           A   

   Runtime                      Genre  IMDB_Rating  \
0  142 min                      Drama          9.3   
1  175 min               Crime, Drama          9.2   
2  152 min       Action, Crime, Drama          9.0   
3  202 min               Crime, Drama          9.0   
4   96 min               Crime, Drama          9.0   
5  201 min   Action, Adventure, Drama          8.9   
6  154 min               Crime, Drama          8.9   
7  195 min  Biography, Drama, History          8.9   
8  148 min  Action, Adventure, Sci-Fi          8.8   
9  139 min                      Drama          8.8   

                                            Overview  Meta_score  \
0  Two imprisoned men bond over a number of years...        80.0   
1  An organized crime dynasty's aging patriarch t...       100.0   
2  When the menace known as the Joker wreaks havo...        84.0   
3  The early life and career of Vito Corleone in ...        90.0   
4  A jury holdout attempts to prevent a miscarria...        96.0   
5  Gandalf and Aragorn lead the World of Men agai...        94.0   
6  The lives of two mob hitmen, a boxer, a gangst...        94.0   
7  In German-occupied Poland during World War II,...        94.0   
8  A thief who steals corporate secrets through t...        74.0   
9  An insomniac office worker and a devil-may-car...        66.0   

               Director              Star1                 Star2  \
0        Frank Darabont        Tim Robbins        Morgan Freeman   
1  Francis Ford Coppola      Marlon Brando             Al Pacino   
2     Christopher Nolan     Christian Bale          Heath Ledger   
3  Francis Ford Coppola          Al Pacino        Robert De Niro   
4          Sidney Lumet        Henry Fonda           Lee J. Cobb   
5         Peter Jackson        Elijah Wood       Viggo Mortensen   
6     Quentin Tarantino      John Travolta           Uma Thurman   
7      Steven Spielberg        Liam Neeson         Ralph Fiennes   
8     Christopher Nolan  Leonardo DiCaprio  Joseph Gordon-Levitt   
9         David Fincher          Brad Pitt         Edward Norton   

               Star3             Star4  No_of_Votes        Gross  
0         Bob Gunton    William Sadler      2343110   28,341,469  
1         James Caan      Diane Keaton      1620367  134,966,411  
2      Aaron Eckhart     Michael Caine      2303232  534,858,444  
3      Robert Duvall      Diane Keaton      1129952   57,300,000  
4      Martin Balsam      John Fiedler       689845    4,360,000  
5       Ian McKellen     Orlando Bloom      1642758  377,845,905  
6  

In [ ]:
# Generate summary statistics
movies_df.describe()

IMDB_Rating  Meta_score   No_of_Votes
count  1000.000000  843.000000  1.000000e+03
mean      7.949300   77.971530  2.736929e+05
std       0.275491   12.376099  3.273727e+05
min       7.600000   28.000000  2.508800e+04
25%       7.700000   70.000000  5.552625e+04
50%       7.900000   79.000000  1.385485e+05
75%       8.100000   87.000000  3.741612e+05
max       9.300000  100.000000  2.343110e+06

In [ ]:
# Plot your data to see what's in your DataFrame
hvplot.show (movies_df.hvplot.line(
    x="Released_Year",
    y="Meta_score",
    width=800,
    height=400,
    rot=90
))

Launching server at http://localhost:38235


---

### Prepare the Data

In [ ]:
movies_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 16 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Poster_Link    1000 non-null   object 
 1   Series_Title   1000 non-null   object 
 2   Released_Year  1000 non-null   object 
 3   Certificate    899 non-null    object 
 4   Runtime        1000 non-null   object 
 5   Genre          1000 non-null   object 
 6   IMDB_Rating    1000 non-null   float64
 7   Overview       1000 non-null   object 
 8   Meta_score     843 non-null    float64
 9   Director       1000 non-null   object 
 10  Star1          1000 non-null   object 
 11  Star2          1000 non-null   object 
 12  Star3          1000 non-null   object 
 13  Star4          1000 non-null   object 
 14  No_of_Votes    1000 non-null   int64  
 15  Gross          831 non-null    object 
dtypes: float64(2), int64(1), object(13)
memory usage: 125.1+ KB


In [ ]:
non_numerical_columns = movies_df.select_dtypes(include=["object"]).columns.tolist()

In [ ]:
movies_df_numerical = movies_df.drop(non_numerical_columns, axis=1)

In [ ]:
scaler = StandardScaler()
movies_df_scaled = scaler.fit_transform(movies_df_numerical)

In [ ]:
# Use the `StandardScaler()` module from scikit-learn to normalize the data from the CSV file

movies_df_scaled[0:5]

array([[4.90533208, 0.16399949, 6.32445085],
       [4.54216246, 1.78097689, 4.11563919],
       [3.81582321, 0.48739497, 6.20257766],
       [3.81582321, 0.97248819, 2.61685696],
       [3.81582321, 1.45758141, 1.27182357]])

In [ ]:
# Create a DataFrame with the scaled data
movies_df_scaled =  pd.DataFrame(movies_df_scaled, columns=(["Poster_Link",
                                                             "Series_Title",
                                                             "Released_Year"
                                                              ]))

# Copy the crypto names from the original data
movies_df_scaled['coin_id'] = movies_df.index

# Set the coinid column as index
movies_df_scaled = movies_df_scaled.set_index('coin_id')

# Display sample data
movies_df_scaled.head()

Poster_Link  Series_Title  Released_Year
coin_id                                          
0           4.905332      0.163999       6.324451
1           4.542162      1.780977       4.115639
2           3.815823      0.487395       6.202578
3           3.815823      0.972488       2.616857
4           3.815823      1.457581       1.271824

---

### Find the Best Value for k Using the Original Data.

In [ ]:
# Create a list with the number of k-values from 1 to 11
inertia = []
k = list(range(1, 11))

In [ ]:
movies_df_scaled.isnull().sum()

Poster_Link        0
Series_Title     157
Released_Year      0
dtype: int64

In [ ]:
movies_df_scaled.dropna(inplace=True)

In [ ]:
# Create an empty list to store the inertia values
inertia = []

# Create a for loop to compute the inertia with each possible value of k
# Inside the loop:
# 1. Create a KMeans model using the loop counter for the n_clusters
# 2. Fit the model to the data using `df_market_data_scaled`
# 3. Append the model.inertia_ to the inertia list
for i in k:
    k_model = KMeans(n_clusters=i, random_state=0)
    k_model.fit(movies_df_scaled)
    inertia.append(k_model.inertia_)


In [ ]:
# Create a dictionary with the data to plot the Elbow curve
elbow_data = {"k": k, "inertia": inertia}
df_elbow = pd.DataFrame(elbow_data)

# Create a DataFrame with the data to plot the Elbow curve
df_elbow.head()

k      inertia
0  1  2655.784062
1  2  1708.627724
2  3  1213.834786
3  4  1009.805290
4  5   846.739914

In [ ]:
# Plot a line chart with all the inertia values computed with
# the different values of k to visually identify the optimal value for k.
df_elbow.hvplot.line(
    x="k",
    y="inertia",
    title="Elbow Curve",
    xticks=k
)

:Curve   [k]   (inertia)

#### Answer the following question:

**Question:** What is the best value for `k`?

**Answer:** It looks like the best value for k is 4 according to the elbow curve above.

---

### Cluster Cryptocurrencies with K-means Using the Original Data

In [ ]:
# Initialize the K-Means model using the best value for k
model = KMeans(n_clusters=4, random_state=2)

In [ ]:
# Fit the K-Means model using the scaled data
model.fit(movies_df_scaled)

KMeans(n_clusters=4, random_state=2)

In [ ]:
# Predict the clusters to group the cryptocurrencies using the scaled data
Movies_clusters = model.predict(movies_df_scaled)

# Print the resulting array of cluster values.
print(Movies_clusters)

[3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 2 2 3 3 2 3 3 3 3 3 3 2 2 2 3 2 3 3 3
 2 3 3 3 3 3 3 2 2 3 2 2 2 2 2 2 2 2 2 3 2 3 3 2 3 2 2 3 2 2 3 2 2 2 2 2 2
 2 2 2 3 2 2 2 2 3 2 2 2 3 2 2 2 2 2 3 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 0 1
 1 2 2 3 2 3 0 2 2 2 3 3 2 2 2 2 2 2 2 2 2 2 2 1 2 2 2 2 0 2 1 2 1 2 1 1 1
 1 1 1 1 1 2 2 1 1 1 2 2 0 2 2 2 2 2 2 1 2 2 2 2 0 2 2 2 2 2 0 1 1 2 2 2 1
 2 1 2 0 2 1 2 1 2 2 2 1 1 2 1 2 2 2 1 1 0 0 1 2 2 2 2 2 1 1 2 1 1 1 1 1 1
 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 2 0 2 2 1 0 0 1 0 2 2 2 2 0 2 0 0 2 0 2 1 0
 0 2 2 0 3 1 2 0 0 2 0 2 1 2 2 2 1 1 1 0 0 1 2 0 2 0 2 1 0 1 1 1 1 1 1 2 1
 1 2 0 0 2 0 2 0 1 0 2 1 1 1 2 1 1 1 1 2 1 1 0 2 1 0 1 0 1 1 1 1 0 0 0 1 1
 1 1 1 1 1 1 1 1 1 1 1 0 1 1 1 1 1 1 1 1 2 1 1 1 1 1 1 0 1 2 2 0 2 2 1 2 1
 1 0 1 1 1 0 1 2 1 1 1 2 0 1 0 2 1 1 0 2 2 1 1 2 1 1 1 0 0 1 2 1 1 2 1 1 1
 0 1 0 0 1 1 1 1 1 1 1 0 1 0 0 1 1 1 0 1 1 1 1 1 1 1 1 0 1 1 1 1 1 1 1 1 0
 1 1 1 0 1 1 1 0 0 2 0 1 0 1 1 1 1 0 0 1 1 0 1 0 1 0 0 1 0 1 0 0 1 0 1 1 1
 0 0 1 0 1 1 2 0 2 0 0 1 

In [ ]:
# Create a copy of the DataFrame
movies_df_scaled_predictions = movies_df_scaled.copy()

In [ ]:
# Add a new column to the DataFrame with the predicted clusters
movies_df_scaled_predictions["MovieCluster"] = Movies_clusters

# Display sample data
movies_df_scaled_predictions.head()

Poster_Link  Series_Title  Released_Year  MovieCluster
coin_id                                                        
0           4.905332      0.163999       6.324451             3
1           4.542162      1.780977       4.115639             3
2           3.815823      0.487395       6.202578             3
3           3.815823      0.972488       2.616857             3
4           3.815823      1.457581       1.271824             3

In [ ]:
movies_df_scaled.head()

Poster_Link  Series_Title  Released_Year
coin_id                                          
0           4.905332      0.163999       6.324451
1           4.542162      1.780977       4.115639
2           3.815823      0.487395       6.202578
3           3.815823      0.972488       2.616857
4           3.815823      1.457581       1.271824

In [ ]:
movies_df_scaled.dtypes

Poster_Link      float64
Series_Title     float64
Released_Year    float64
dtype: object

In [ ]:
# Create a scatter plot using hvPlot by setting
# `x="price_change_percentage_24h"` and `y="price_change_percentage_7d"`.
# Color the graph points with the labels found using K-Means and
# add the crypto name in the `hover_cols` parameter to identify
# the cryptocurrency represented by each data point.
scatter_plot = movies_df_scaled_predictions.hvplot.scatter(
    x= "Poster_Link",
    y= "Series_Title",
    by= "Released_Year",
    hover_cols=["coin_id"],
    title = "Scatter Plot by Crypto Currency Using Scaled Data"
)
scatter_plot

:NdOverlay   [Released_Year]
   :Scatter   [Poster_Link]   (Series_Title,coin_id)

---

### Optimize Clusters with Principal Component Analysis.

In [ ]:
# Create a PCA model instance and set `n_components=3`.
pca=PCA(n_components=3)

In [ ]:
# Use the PCA model with `fit_transform` to reduce to
# three principal components.
clusters_pca = pca.fit_transform(movies_df_scaled)
# View the first five rows of the DataFrame.
clusters_pca[:5]

array([[ 7.6766873 ,  2.02043211, -0.44065469],
       [ 6.34192904, -0.32197192,  0.15677376],
       [ 6.90538896,  1.74913803, -1.23938222],
       [ 4.63528549, -0.14024114,  0.85097299],
       [ 3.85730145, -1.1255816 ,  1.53527941]])

In [ ]:
# Retrieve the explained variance to determine how much information
# can be attributed to each principal component.
pca.explained_variance_ratio_

array([0.55580488, 0.326576  , 0.11761912])

In [ ]:
# Create the PCA DataFrame
clusters_pca_df = pd.DataFrame(
    clusters_pca,
    columns=["PCA1", "PCA2", "PCA3"]
)
# Copy the crypto names from the original data
clusters_pca_df['coin_id'] = list(movies_df_scaled_predictions.index)
clusters_pca_df

# Set the coinid column as index
clusters_pca_df = clusters_pca_df.set_index('coin_id')

# Review the PCA DataFrame
clusters_pca_df.head()

PCA1      PCA2      PCA3
coin_id                              
0        7.676687  2.020432 -0.440655
1        6.341929 -0.321972  0.156774
2        6.905389  1.749138 -1.239382
3        4.635285 -0.140241  0.850973
4        3.857301 -1.125582  1.535279

#### Answer the following question:

**Question:** What is the total explained variance of the three principal components?

**Answer:**

In [ ]:
# Create a new DataFrame with the PCA data.
model = KMeans(n_clusters=3, random_state=0)

# Creating a DataFrame with the PCA data
model.fit(clusters_pca_df)

# Copy the crypto names from the original data
k_3 = model.predict(clusters_pca_df)

# Set the coinid column as index
clusters_pca_predictions = clusters_pca_df.copy()

# Display sample data
clusters_pca_predictions["customer_segments"] = k_3

In [ ]:
# Plot the clusters
clusters_pca_predictions.hvplot.scatter(
    x="PCA1",
    y="PCA3",
    by="customer_segments"
)

:NdOverlay   [customer_segments]
   :Scatter   [PCA1]   (PCA3)

---

### Find the Best Value for k Using the PCA Data

In [ ]:
# Create a list with the number of k-values from 1 to 11
inertia = []
k = list(range(1, 11))

In [ ]:
# Create an empty list to store the inertia values
inertia = []

# Create a for loop to compute the inertia with each possible value of k
# Inside the loop:
# 1. Create a KMeans model using the loop counter for the n_clusters
# 2. Fit the model to the data using `df_market_data_pca`
# 3. Append the model.inertia_ to the inertia list
for i in k:
    k_model = KMeans(n_clusters=i, random_state=3)
    k_model.fit(clusters_pca_df)
    inertia.append(k_model.inertia_)

In [ ]:
# Create a dictionary with the data to plot the Elbow curve
elbow_data_2 = {"k": k, "inertia": inertia}
# Create a DataFrame with the data to plot the Elbow curve
df_elbow_2 = pd.DataFrame(elbow_data_2)
df_elbow_2.head()

k      inertia
0  1  2655.784062
1  2  1708.635122
2  3  1214.034698
3  4  1009.805290
4  5   846.079918

In [ ]:
# Plot a line chart with all the inertia values computed with
# the different values of k to visually identify the optimal value for k.
df_elbow_2.hvplot.line(
    x="k",
    y="inertia",
    title="Elbow Curve",
    xticks=k
)

:Curve   [k]   (inertia)

#### Answer the following questions:

* **Question:** What is the best value for `k` when using the PCA data?

  * **Answer:**The best value for k is 4.


* **Question:** Does it differ from the best k value found using the original data?

  * **Answer:**  It is the same as the original data.

### Cluster Cryptocurrencies with K-means Using the PCA Data

In [ ]:
# Initialize the K-Means model using the best value for k
model = KMeans(n_clusters=4, random_state=0)

In [ ]:
# Fit the K-Means model using the PCA data
model.fit(clusters_pca_predictions)

KMeans(n_clusters=4, random_state=0)

In [ ]:
# Predict the clusters to group the cryptocurrencies using the PCA data
k_3 = model.predict(clusters_pca_predictions)
# Print the resulting array of cluster values.
print(clusters_pca_predictions)

             PCA1      PCA2      PCA3  customer_segments
coin_id                                                 
0        7.676687  2.020432 -0.440655                  1
1        6.341929 -0.321972  0.156774                  1
2        6.905389  1.749138 -1.239382                  1
3        4.635285 -0.140241  0.850973                  1
4        3.857301 -1.125582  1.535279                  1
...           ...       ...       ...                ...
995     -1.186870  0.045331 -0.516182                  0
996     -1.299530 -0.708232 -0.475088                  2
997     -1.260989 -0.770543 -0.519540                  2
998     -1.432707 -0.274941 -0.300793                  0
999     -1.086798 -1.350311 -0.748751                  2

[843 rows x 4 columns]


In [ ]:
# Create a copy of the DataFrame with the PCA data
clusters_pca_predictions_df = clusters_pca_df.copy()

# Add a new column to the DataFrame with the predicted clusters
clusters_pca_predictions_df["customer_segments"] = k_3

# Display sample data
clusters_pca_predictions_df.head()

PCA1      PCA2      PCA3  customer_segments
coin_id                                                 
0        7.676687  2.020432 -0.440655                  2
1        6.341929 -0.321972  0.156774                  2
2        6.905389  1.749138 -1.239382                  2
3        4.635285 -0.140241  0.850973                  2
4        3.857301 -1.125582  1.535279                  2

In [ ]:
# Create a scatter plot using hvPlot by setting
# `x="PC1"` and `y="PC2"`.
# Color the graph points with the labels found using K-Means and
# add the crypto name in the `hover_cols` parameter to identify
# the cryptocurrency represented by each data point.
clusters_pca_predictions_df.hvplot.scatter(
    x="PCA1",
    y="PCA2",
    by="customer_segments",
    hover_cols="coin_id"
)

:NdOverlay   [customer_segments]
   :Scatter   [PCA1]   (PCA2,coin_id)

### Visualize and Compare the Results

In this section, you will visually analyze the cluster analysis results by contrasting the outcome with and without using the optimization techniques.

In [ ]:
# Composite plot to contrast the Elbow curves
e_1 = df_elbow.hvplot.line(x="k", y="inertia", title= "Elbow Curve 1", xticks=k)
e_2 = df_elbow_2.hvplot.line(x="k", y="inertia", title="Elbow Curve 2", xticks=k)
e_1 + e_2

:Layout
   .Curve.I  :Curve   [k]   (inertia)
   .Curve.II :Curve   [k]   (inertia)

In [ ]:
# Composite plot to contrast the clusters
c1 = movies_df_scaled_predictions.hvplot.scatter( x='Poster_Link', y='Series_Title', by='Released_Year', hover_cols = 'coin_id')
c2 = clusters_pca_predictions_df.hvplot.scatter(x="PCA1", y="PCA2", by = 'customer_segments', hover_cols='coin_id')

In [ ]:
c1 + c2

:Layout
   .NdOverlay.I  :NdOverlay   [Released_Year]
      :Scatter   [Poster_Link]   (Series_Title,coin_id)
   .NdOverlay.II :NdOverlay   [customer_segments]
      :Scatter   [PCA1]   (PCA2,coin_id)

#### Answer the following question:

  * **Question:** After visually analyzing the cluster analysis results, what is the impact of using fewer features to cluster the data using K-Means?

  * **Answer:** The clusters become more distinct and easier to see visually. PCA removes less informative features from the data, as it retains the most significance variance in the original dataset. The second scatterplot above for PCA, shows four distinct clusters, with 'ethland' in orange and 'celsius-degree-token' in yellow. There two cryptocurrencies incidently showed significantly higher percentage price change at 200d and 1 year, compared to all the other cryptocurrencies. Splitting these two out into their own clusters makes sense.